In [81]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy import interpolate
import h5py
import time

In [82]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [83]:
from bender_functions import Bender

In [84]:
bender = Bender()

# Set up movement and activation

## Details about the fish and prep

In [85]:
fishcode = "scup006"

Basic measurements for the fish

In [86]:
fishlen = 225       # mm
fishmass = 155      # g

Location of the bending point along the body. Distance from the head to the bending point

In [87]:
dbend = 88          # mm

Distance between the two clamps:

In [88]:
dclamp = 13         # mm

Vertical and horizontal distance from the transducer to the center of pressure on the fish

In [89]:
dvert = 53          # mm
dhoriz = 0          # mm

Cross sectional size of the fish

In [90]:
xsec_width = 20          # mm
xsec_height = 58         # mm

## Output file

In [91]:
outputfile = 'C:\\Data\\scup\\test_001.h5'
outputfile = bender.increment_file_name(outputfile)

print('Actual output file: {}'.format(outputfile))

Actual output file: C:\Data\scup\test_004.h5


## Movement parameters

In [117]:
duration = 30       # sec
startfreq = 8.0     # Hz
endfreq = 1.0       # Hz
amp = 10            # deg
amplitude_frequency_exponent = -0.5       # should be between -1 and 0

scale = 6       # output teeth divided by input teeth

waitbefore = 3.0
waitafter = 1.0

The amplitude frequency exponent changes the amplitude as the frequency changes. If `amplitude_frequency_exponent` is 0, the amplitude in terms of angle is constant, but angular velocity increases as frequency increases. If `amplitude_frequency_exponent` is -1, the amplitude in terms of angular velocity is constant, but the angle decreases as frequency increases. A value of 0.5 is often a good compromise.

# Sampling parameters and channels

Sampling parameters

In [118]:
samplefreq = 1000.0
outputfreq = 100000.0

In [119]:
device_name = '/Dev1'

## Digital output channel

Controls the motor

In [120]:
bender.set_motor_channel('port0')

## Analog output channel

We don't use the analog output for frequency sweeps, but we still need to set up the channels to get the timing to work properly

In [121]:
bender.set_activation_channels('ao0', 'ao1')

## Analog input channels

Six channels from the force transducer, plus the monitor channel from the S88 stimulator.

In [122]:
SG1_chan = 'ai0'
SG2_chan = 'ai1'
SG3_chan = 'ai2'
SG4_chan = 'ai3'
SG5_chan = 'ai4'
SG6_chan = 'ai5'

In [123]:
activation_monitor_chan = 'ai6'

In [124]:
inchannels = [SG1_chan, SG2_chan, SG3_chan, SG4_chan, SG5_chan, SG6_chan,
                activation_monitor_chan]
inchannel_names = ['SG1', 'SG2', 'SG3', 'SG4', 'SG5', 'SG6',
                    'activation_monitor']

bender.set_input_channels(inchannels, inchannel_names)

Force transducer calibration file

In [125]:
bender.loadCalibration('FT17161.cal')
bender.calibration

array([[ 9.609000e-02, -2.877000e-01,  1.039313e+01, -2.850000e-03,
        -1.706000e-01, -2.490000e-03],
       [ 5.423000e-02, -7.349830e+00,  2.909400e-01, -4.012000e-02,
        -4.740000e-03, -8.726000e-02],
       [-7.387000e-02,  8.691000e-02,  1.065666e+01,  1.484400e-01,
         8.860000e-02,  0.000000e+00],
       [ 6.261130e+00,  3.686710e+00, -4.922800e-01,  1.253000e-02,
        -3.947000e-02, -8.481000e-02],
       [-7.690000e-03, -6.688000e-02,  1.045477e+01, -1.517300e-01,
         8.331000e-02,  1.500000e-04],
       [-6.235270e+00,  3.543590e+00, -3.817600e-01,  2.526000e-02,
         3.202000e-02, -8.559000e-02]])

## Encoder angle input

In [126]:
encoder_counts_per_rev = 10000
bender.set_encoder_channel('ctr0', counts_per_rev=encoder_counts_per_rev)

Start setting up the output

In [127]:
totaldur = waitbefore + duration + waitafter

t = np.arange(0, totaldur, 1.0/samplefreq)
t -= waitbefore

Generate the angle and angular velocity signals

In [128]:
lnk = 1.0/duration * (np.log(endfreq) - np.log(startfreq))

f = startfreq * np.exp(t * lnk)

tnorm = 2*np.pi*startfreq * (np.exp(t * lnk) - 1) / lnk

tnorm[t < 0] = -1
tnorm[t > duration] = np.ceil(np.max(tnorm))

A0 = startfreq ** amplitude_frequency_exponent

angle = amp / A0 * np.power(f, amplitude_frequency_exponent) * np.sin(tnorm)
anglevel = amp / A0 * np.exp(amplitude_frequency_exponent * t * lnk) * lnk * \
    (amplitude_frequency_exponent * np.sin(tnorm) + 2*np.pi/lnk * f * np.cos(tnorm))

f[t < 0] = np.nan
f[t > duration] = np.nan

angle[t < 0] = 0
angle[t > duration] = 0

anglevel[t < 0] = 0
anglevel[t > duration] = 0

isramp = (t >= duration) & (t < duration+0.5)
k = int((waitbefore + duration) * samplefreq)

pend = angle[k]
velend = (0 - pend) / 0.5

ramp = pend + (t[isramp] - t[k])*velend

np.place(anglevel, isramp, velend)
np.place(angle, isramp, ramp)


In [129]:
bender.set_bending_signal(t, angle, anglevel)

and plot them:

In [130]:
fig = make_subplots(rows = 2, cols = 1,
                   shared_xaxes=True)
fig.add_trace(
    go.Scatter(x = t, y = angle, mode="lines", name="angle"),
    row=1, col=1)

fig.update_yaxes(title_text = "angle (deg)", row=1)
fig.add_trace(
    go.Scatter(x = t, y = anglevel, mode="lines", name="anglevel"),
    row=2, col=1)

fig.update_yaxes(title_text = "angular velocity (deg/s)", row=2)
fig.update_xaxes(title_text = "time (s)", row=2)

Generate the motor step and direction pulses. 

In [131]:
tout, dig, step, direction = bender.make_motor_stepper_pulses(outputfreq,
                        scale=scale,
                        stepsperrev=1600)

Use the cell below to debug the step and direction pulses, but don't render it every time. It takes a long time to plot the traces, because the output sampling rate is high.

In [132]:
# fig = make_subplots()
# fig.add_trace(go.Scatter(x=tout, y=step, mode="lines", name="step"))
# fig.add_trace(go.Scatter(x=tout, y=direction, mode="lines", name="dir"))
# fig.add_trace(go.Scatter(x=tout, y=dig, mode="lines", name="port"))

# Do data acquisition

## Main code block

Sets up the DAQ, sends the output, records the input, and writes it to the file.

In [133]:
aidata = bender.run(device_name)


In [134]:
forcetorque = bender.applyCalibration(aidata)
forcetorque_names = ['xForce', 'yForce', 'zForce', 'xTorque', 'yTorque', 'zTorque']

In [135]:
with h5py.File(outputfile, 'w') as f:
    f.attrs['EndTime'] = bender.endTime.strftime('%Y-%m-%d %H:%M:%S %Z')
    f.attrs['FishCode'] = fishcode
    f.attrs['FishLength_mm'] = fishlen
    f.attrs['FishMass_g'] = fishmass
    f.attrs['FishCrossSectionWidth_mm'] = xsec_width
    f.attrs['FishCrossSectionHeight_mm'] = xsec_height

    f.attrs['BendLocation_mm'] = dbend
    f.attrs['ClampDistance_mm'] = dclamp
    f.attrs['DistanceFromTransducerVert_mm'] = dvert
    f.attrs['DistanceFromTransducerHoriz_mm'] = dhoriz
    
    gin = f.create_group('RawInput')
    gin.attrs['SampleFrequency'] = samplefreq
    gin.create_dataset('forcetransducer', data=aidata[:6,:])
    gin.create_dataset('activation_monitor', data=aidata[6,:])

    gcal = f.create_group('Calibrated')
    for ft1, name1 in zip(forcetorque, forcetorque_names):
        gcal.create_dataset(name1, data=ft1)
    gcal.create_dataset('CalibrationMatrix', data=bender.calibration)

    ds = gcal.create_dataset('Encoder', data=bender.angledata)
    ds.attrs['CountsPerRev'] = encoder_counts_per_rev

    # save the output data
    gout = f.create_group('Output')
    gout.attrs['SampleFrequency'] = outputfreq
    gout.create_dataset('DigitalOut', data=dig)
    
    # save the parameters for generating the stimulus
    gout = f.create_group('NominalStimulus')
    gout.attrs['Type'] = 'Frequency Sweep'
    
    gout.create_dataset('t', data=t)
    ds = gout.create_dataset('Position', data=angle)
    ds.attrs['Units'] = 'deg'
    ds = gout.create_dataset('Velocity', data=anglevel)
    ds.attrs['Units'] = 'deg/sec'
    gout.create_dataset('tnorm', data=tnorm)

    gout.attrs['Amplitude'] = amp
    gout.attrs['Duration'] = duration
    gout.attrs['StartFrequency'] = startfreq
    gout.attrs['EndFrequency'] = endfreq
    gout.attrs['AmplitudeFrequencyExponent'] = amplitude_frequency_exponent
    gout.attrs['WaitPre'] = waitbefore
    gout.attrs['WaitPost'] = waitafter
    gout.attrs['ScaleFactor'] = scale

    gout.attrs['ActivationOn'] = False
    


In [136]:
fig = make_subplots(rows = 2, cols = 1,
                   shared_xaxes=True)
fig.add_trace(
    go.Scatter(x = t, y = angle, mode="lines", name="angle"),
    row=1, col=1)
fig.add_trace(
    go.Scatter(x = t, y = forcetorque[3,:], mode="lines", name="Tx"),
    row=2, col=1)

fig.update_yaxes(title_text = "angle (deg)", row=1)
fig.update_yaxes(title_text = "torque (Nm)", row=2)
fig.update_xaxes(title_text = "time (s)", row=2)


In [137]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=angle, y=forcetorque[3,:]))
fig.update_yaxes(title_text="torque (Nm)")
fig.update_xaxes(title_text="angle (deg)")